In [71]:
import pandas as pd

# Replace 'your_file.csv' with the path to your file
file_path = './Synthetic-Persona-Chat/data/Synthetic-Persona-Chat_test.csv'
df = pd.read_csv(file_path)

# Display the first few rows of the dfframe
print(df.head())

                                     user 1 personas  \
0  I just bought a brand new house.\nI like to da...   
1  I am an old man.\nI have a wheelchair that is ...   
2  I met my best friend in kindergarten.\nI am of...   
3  I love having facial hair.\nI hope to retire s...   
4  I love watching movies and tv.\nI have a husba...   

                                     user 2 personas  \
0  I love to meet new people.\nI have a turtle na...   
1  I drive a ford pickup truck.\nI am very conser...   
2  I have two dogs and one cat.\nI work as a nurs...   
3  I am happy being single and alone.\nI only dri...   
4  I am afraid of heights.\nI love animals and ha...   

                         Best Generated Conversation  
0  User 1: Hi, I'm [User 1's name]. What's your n...  
1  User 1: Hi there!\nUser 2: Hello.\nUser 1: I'm...  
2  User 1: Hi! What do you do for work?\nUser 2: ...  
3  User 1: How are you doing today?\nUser 2: I'm ...  
4  User 1: Hi there!\nUser 2: Hi there!\nUser 1: ..

In [72]:
data_list = df.to_dict(orient='records')

In [73]:
data_list[0:5]

[{'user 1 personas': 'I just bought a brand new house.\nI like to dance at the club.\nI run a dog obedience school.\nI have a big sweet tooth.\nI like taking and posting selkies.',
  'user 2 personas': 'I love to meet new people.\nI have a turtle named timothy.\nMy favorite sport is ultimate frisbee.\nMy parents are living in bora bora.\nAutumn is my favorite season.',
  'Best Generated Conversation': "User 1: Hi, I'm [User 1's name]. What's your name?\nUser 2: Hi, I'm [User 2's name]. It's nice to meet you.\nUser 1: Nice to meet you too. What are you interested in?\nUser 2: I like to meet new people, play ultimate frisbee, and spend time with my family.\nUser 1: Those are all great things to be interested in. I like to dance at the club, run a dog obedience school, and eat a lot of sweets.\nUser 2: That's interesting. I've never met anyone who runs a dog obedience school before.\nUser 1: It's a lot of fun. I get to work with dogs every day and help them learn how to behave.\nUser 2: T

In [74]:
data_list = [{"persona":instance["user 1 personas"],"conversation":instance["Best Generated Conversation"]} for instance in data_list]

In [75]:
for i, instance in enumerate(data_list):
    try:
        instance["persona"] = instance["persona"].split("\n")
        instance["conversation"] = instance["conversation"].split("\n")
        instance["persona"] = [p.strip() for p in instance["persona"] if p.strip()]
        instance["conversation"] = [c.strip() for c in instance["conversation"] if c.strip()]
        
        instance["persona"] = [p + "</s>" for p in instance["persona"]]

        instance["conversation"] = [c.replace("User 1:", "<query>") for c in instance["conversation"]]
        instance["conversation"] = [c.replace("User 2:", "<responce>") + "</s>" for c in instance["conversation"]]
    except Exception as e:
        print("Error in instance:", instance)
        print("Error in instance index:", i)
        print("Exception:", e)
        continue

Error in instance: {'persona': ['I love playing video games.', 'Hey there my name is jordan and i am a veterinarian.', 'I am also a musician on the weekends.', 'Love to read drama books.'], 'conversation': nan}
Error in instance index: 510
Exception: 'float' object has no attribute 'split'


In [94]:
len(data_list[5]['conversation'])
data_list[5]['conversation']


["<query> Hi, I'm [user 1's name].</s>",
 "<responce> Hi, I'm [user 2's name].</s>",
 '<query> Nice to meet you! What do you do for a living?</s>',
 "<responce> I'm a pediatrician.</s>",
 "<query> Oh, that's great! I'm an attorney.</s>",
 "<responce> Really? That's cool. What kind of law do you practice?</s>",
 '<query> I do family law.</s>',
 "<responce> Oh, interesting. I don't know much about family law.</s>",
 "<query> It's a lot of work, but it's also very rewarding.</s>",
 '<responce> I can imagine. What do you like about it the most?</s>',
 '<query> I like helping people and making a difference in their lives.</s>',
 "<responce> That's a great goal.</s>",
 '<query> Thanks. What do you like about being a pediatrician?</s>',
 "<responce> I love working with kids. They're always so funny and honest.</s>",
 "<query> I can imagine. I'm sure it's a lot of fun.</s>",
 '<responce> It is. I also like being able to help families with their children.</s>',
 "<query> That's great. It sounds

In [108]:
data = data_list[5]['conversation']

history_windows = []

for i in range(len(data)):
    if data[i].startswith("<query>"):
        window = []
        # add the query itself first
        window.append(data[i])
        
        # move backwards and collect previous turns (up to 5)
        j = i - 1
        while j >= 0 and len(window) < 5:
            window.insert(0, data[j])
            j -= 1
        
        history_windows.append(window)

# Display results
for idx, history in enumerate(history_windows):
    print(f"Window {idx+1}:")
    for line in history:
        print("  ", line)
    print()


Window 1:
   <query> Hi, I'm [user 1's name].</s>

Window 2:
   <query> Hi, I'm [user 1's name].</s>
   <responce> Hi, I'm [user 2's name].</s>
   <query> Nice to meet you! What do you do for a living?</s>

Window 3:
   <query> Hi, I'm [user 1's name].</s>
   <responce> Hi, I'm [user 2's name].</s>
   <query> Nice to meet you! What do you do for a living?</s>
   <responce> I'm a pediatrician.</s>
   <query> Oh, that's great! I'm an attorney.</s>

Window 4:
   <query> Nice to meet you! What do you do for a living?</s>
   <responce> I'm a pediatrician.</s>
   <query> Oh, that's great! I'm an attorney.</s>
   <responce> Really? That's cool. What kind of law do you practice?</s>
   <query> I do family law.</s>

Window 5:
   <query> Oh, that's great! I'm an attorney.</s>
   <responce> Really? That's cool. What kind of law do you practice?</s>
   <query> I do family law.</s>
   <responce> Oh, interesting. I don't know much about family law.</s>
   <query> It's a lot of work, but it's also ve

In [126]:
def get_history_windows(data, window_size=5):
    history_windows = []

    for i in range(len(data)):
        if data[i].startswith("<query>"):
            window = []
            # add the query itself first
            window.append(data[i])

            # move backwards and collect previous turns (up to window_size)
            j = i - 1
            while j >= 0 and len(window) < window_size:
                window.insert(0, data[j])
                j -= 1

            history_windows.append(window)

    return history_windows


In [127]:
for data in get_history_windows(data_list[5]['conversation']):
    print(data)
    break

["<query> Hi, I'm [user 1's name].</s>"]


In [142]:
conversation = [ d for d in get_history_windows(instance['conversation'])]

In [143]:
conversation

[['<query> Hi there!</s>'],
 ['<query> Hi there!</s>',
  '<responce> Hi there!</s>',
  "<query> What's up?</s>"],
 ['<query> Hi there!</s>',
  '<responce> Hi there!</s>',
  "<query> What's up?</s>",
  "<responce> Not much. I'm just hanging out at home.</s>",
  "<query> Me too! I'm just watching some TV.</s>"],
 ["<query> What's up?</s>",
  "<responce> Not much. I'm just hanging out at home.</s>",
  "<query> Me too! I'm just watching some TV.</s>",
  '<responce> Oh, what are you watching?</s>',
  "<query> I'm watching a rap music video.</s>"],
 ["<query> Me too! I'm just watching some TV.</s>",
  '<responce> Oh, what are you watching?</s>',
  "<query> I'm watching a rap music video.</s>",
  '<responce> Oh, cool! I love rap music.</s>',
  "<query> Me too! Who's your favorite rapper?</s>"],
 ["<query> I'm watching a rap music video.</s>",
  '<responce> Oh, cool! I love rap music.</s>',
  "<query> Me too! Who's your favorite rapper?</s>",
  '<responce> I like Drake and Kendrick Lamar.</s>'

In [148]:
from itertools import chain

flattened_data = list(chain.from_iterable(history_windows))
print(flattened_data)

["<query> Hi, I'm [user 1's name].</s>", "<query> Hi, I'm [user 1's name].</s>", "<responce> Hi, I'm [user 2's name].</s>", '<query> Nice to meet you! What do you do for a living?</s>', "<query> Hi, I'm [user 1's name].</s>", "<responce> Hi, I'm [user 2's name].</s>", '<query> Nice to meet you! What do you do for a living?</s>', "<responce> I'm a pediatrician.</s>", "<query> Oh, that's great! I'm an attorney.</s>", '<query> Nice to meet you! What do you do for a living?</s>', "<responce> I'm a pediatrician.</s>", "<query> Oh, that's great! I'm an attorney.</s>", "<responce> Really? That's cool. What kind of law do you practice?</s>", '<query> I do family law.</s>', "<query> Oh, that's great! I'm an attorney.</s>", "<responce> Really? That's cool. What kind of law do you practice?</s>", '<query> I do family law.</s>', "<responce> Oh, interesting. I don't know much about family law.</s>", "<query> It's a lot of work, but it's also very rewarding.</s>", '<query> I do family law.</s>', "<r

In [170]:
train_data = [
    "<latent>" + "<person>" + " ".join(instance['persona']) + " " + " ".join(window)
    for instance in data_list
    if isinstance(instance['conversation'], list)  # Only process if 'conversation' is a list
    for window in get_history_windows(instance['conversation'])
]

for da in train_data:
    print(da)


<latent><person>I just bought a brand new house.</s> I like to dance at the club.</s> I run a dog obedience school.</s> I have a big sweet tooth.</s> I like taking and posting selkies.</s> <query> Hi, I'm [User 1's name]. What's your name?</s>
<latent><person>I just bought a brand new house.</s> I like to dance at the club.</s> I run a dog obedience school.</s> I have a big sweet tooth.</s> I like taking and posting selkies.</s> <query> Hi, I'm [User 1's name]. What's your name?</s> <responce> Hi, I'm [User 2's name]. It's nice to meet you.</s> <query> Nice to meet you too. What are you interested in?</s>
<latent><person>I just bought a brand new house.</s> I like to dance at the club.</s> I run a dog obedience school.</s> I have a big sweet tooth.</s> I like taking and posting selkies.</s> <query> Hi, I'm [User 1's name]. What's your name?</s> <responce> Hi, I'm [User 2's name]. It's nice to meet you.</s> <query> Nice to meet you too. What are you interested in?</s> <responce> I like 

In [171]:
len(train_data)

13488

In [14]:
from torch.utils.data import Dataset

In [ ]:
# Convert to torch dataset
class CNNDailyMailDataset(Dataset):
    def __init__(self, data):
        self.input_ids = []

    def __len__(self):
       

    def __getitem__(self, idx):
        